In [1]:
# description of this dataset http://groupware.les.inf.puc-rio.br/har#ixzz2PyRdbAfA
from sklearn import datasets
from sklearn import preprocessing as pp
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold
from sklearn.metrics import confusion_matrix
from sklearn.metrics import recall_score
import numpy
import csv
import pandas as pd
import time

le = pp.LabelEncoder() 
le.fit(['sitting', 'walking', 'sittingdown', 'standing', 'standingup'])

### Retrieving all data
overall = pd.read_csv("./dataset-har-PUC-Rio-ugulino.csv", delimiter=';', header='infer') 
data = overall.loc[:, "x1":"z4"].as_matrix() # has to be converted to ndarray in order to be processed by segment_signal()
targets = overall.loc[:,"class,,"].as_matrix() # double commas: looks like the researchers are naughty

# print type(data)
# print type(targets)
# print data.shape
# print targets.shape


def debug(item, shape=True):
    print item
    print type(item)
    if (shape == True):
        print item.shape()
    print "----------------------"

### Data segmentation: shall use a sudden change of sensor readings
### like if (x_pre - x_curr <= 1.0, do nothing)
### Range of Accelerometer sensor readings is +3g/-3g

# reading 14 sets of data in every 2 seconds. 
# For segmenting the data from online only. 
# each set of data is taken 150ms apart from another.
# so choosing a window size of 14 will be 2.1 seconds.


def segment_signal(data, window_size=14): 

    N = data.shape[0]
    dim = data.shape[1]
    K = N/window_size
    segments = numpy.empty((K, window_size, dim))
    for i in range(K):
        segment = data[i*window_size:i*window_size+window_size,:]
        segments[i] = numpy.vstack(segment)
    return segments

##!!!! questions: for normalization, should it be done right after loading csv or after segmenation? 
##!!!! Normalize() can't process nadarray with dimension > 2.
X = pp.normalize(data)
y = targets[::14] 
y = y[:-1]# -1 because it will have a extra set of data than X.

segs = segment_signal(X)

### feautre extraction // take the difference between sensors

### this method is to extract the difference between consecutive sensor readings.
## parameter raw is a 2D ndarray
## return a 2D ndarray
def extract_diff(raw):

    N = raw.shape[0] # number of sets of sensor readings
    dim = raw.shape[1] # number of values in each readings
    features = numpy.empty((N - 1, dim))
    for i in range(1, N):
        for j in range(dim):
            features[i-1][j] = raw[i][j] - raw[i-1][j]

    return features

def extract_diff_2(raw):

    N = raw.shape[0] # number of segments of sensor readings ()
    I = raw.shape[1] # number of sets of readings (14)
    J = raw.shape[2] # number of values in each set of readings (12)
    feature_num = (I - 1) * J
    feature = numpy.empty((feature_num))
    features = numpy.empty((N, feature_num))
    for n in range(N):
        idx = 0;
        for i in range(1, I):
            for j in range(J):
                feature[idx] = raw[n][i][j] - raw[n][i-1][j]
                idx += 1
        numpy.append(features[n], feature)
        print "---------feature:"
        print feature
        print "---------features[n]:"
        print features[n]
        
    return features

feat = extract_diff_2(segs)

feat

array([[ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       ..., 
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.],
       [ 0.,  0.,  0., ...,  0.,  0.,  0.]])

In [4]:
# description of this dataset http://groupware.les.inf.puc-rio.br/har#ixzz2PyRdbAfA
from sklearn import datasets
from sklearn import preprocessing as pp
from sklearn.neural_network import MLPClassifier
from sklearn.model_selection import train_test_split
from sklearn.model_selection import KFold
from sklearn.metrics import confusion_matrix
from sklearn.metrics import recall_score
import numpy
import csv
import pandas as pd
import time

le = pp.LabelEncoder() 
le.fit(['sitting', 'walking', 'sittingdown', 'standing', 'standingup'])

### Retrieving all data
overall = pd.read_csv("./dataset-har-PUC-Rio-ugulino.csv", delimiter=';', header='infer') 
data = overall.loc[:, "x1":"z4"].as_matrix() # has to be converted to ndarray in order to be processed by segment_signal()
targets = overall.loc[:,"class,,"].as_matrix() # double commas: looks like the researchers are naughty

# print type(data)
# print type(targets)
# print data.shape
# print targets.shape


def debug(item, shape=True):
    print item
    print type(item)
    if (shape == True):
        print item.shape()
    print "----------------------"

### Data segmentation: shall use a sudden change of sensor readings
### like if (x_pre - x_curr <= 1.0, do nothing)
### Range of Accelerometer sensor readings is +3g/-3g

# reading 14 sets of data in every 2 seconds. 
# For segmenting the data from online only. 
# each set of data is taken 150ms apart from another.
# so choosing a window size of 14 will be 2.1 seconds.


def segment_signal(data, window_size=14): 

    N = data.shape[0]
    dim = data.shape[1]
    K = N/window_size
    segments = numpy.empty((K, window_size, dim))
    for i in range(K):
        segment = data[i*window_size:i*window_size+window_size,:]
        segments[i] = numpy.vstack(segment)
    return segments

##!!!! questions: for normalization, should it be done right after loading csv or after segmenation? 
##!!!! Normalize() can't process nadarray with dimension > 2.
X = pp.normalize(data)
y = targets[::14] 
y = y[:-1]# -1 because it will have a extra set of data than X.

segs = segment_signal(X)

### feautre extraction // take the difference between sensors

### this method is to extract the difference between consecutive sensor readings.
## parameter raw is a 2D ndarray
## return a 2D ndarray
def extract_diff(raw):

    N = raw.shape[0] # number of sets of sensor readings
    dim = raw.shape[1] # number of values in each readings
    features = numpy.empty((N - 1, dim))
    for i in range(1, N):
        for j in range(dim):
            features[i-1][j] = raw[i][j] - raw[i-1][j]

    return features

def extract_diff_2(raw):

    N = raw.shape[0] # number of segments of sensor readings ()
    I = raw.shape[1] # number of sets of readings (14)
    J = raw.shape[2] # number of values in each set of readings (12)
    feature_num = (I - 1) * J
    feature = numpy.empty((feature_num))
    features = numpy.empty((N, feature_num))
    for n in range(N):
        idx = 0;
        for i in range(1, I):
            for j in range(J):
                feature[idx] = raw[n][i][j] - raw[n][i-1][j]
                idx += 1
        numpy.append(features[n], feature)
        print features
        print features.shape
        print "---------------------------"
    return features

feat = extract_diff_2(segs)

feat

[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -

---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0

(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 

(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 

---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0

...

(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 

(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 

---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0

(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 0.00239637  0.23005184 -0.29235754 ..., -0.49743294 -0.17449218
  -0.47659805]]
(11830, 156)
---------------------------
[[-0.01013149  0.31069913 -0.21276136 ..., -0.5059926  -0.35317604
  -0.4924089 ]
 [ 0.          0.32804547 -0.20629664 ..., -0.52461956 -0.34184887
  -0.47723456]
 [ 0.01012601  0.33753363 -0.20589552 ..., -0.57849997 -0.3221193
  -0.45030964]
 ..., 
 [-0.08017998  0.11319527 -0.3254364  ..., -0.25154313 -0.08913907
  -0.20514197]
 [-0.08529687  0.28269821 -0.36312097 ..., -0.22611662 -0.07500454
  -0.19854142]
 [ 

array([[-0.01013149,  0.31069913, -0.21276136, ..., -0.5059926 ,
        -0.35317604, -0.4924089 ],
       [ 0.        ,  0.32804547, -0.20629664, ..., -0.52461956,
        -0.34184887, -0.47723456],
       [ 0.01012601,  0.33753363, -0.20589552, ..., -0.57849997,
        -0.3221193 , -0.45030964],
       ..., 
       [-0.08017998,  0.11319527, -0.3254364 , ..., -0.25154313,
        -0.08913907, -0.20514197],
       [-0.08529687,  0.28269821, -0.36312097, ..., -0.22611662,
        -0.07500454, -0.19854142],
       [ 0.00239637,  0.23005184, -0.29235754, ..., -0.49743294,
        -0.17449218, -0.47659805]])